## Uczenie głębokie – przetwarzanie tekstu – laboratoria
# 3. RNN

RNN - rekurencyjna sieć neuronowa \
NEP - oznaczanie jednostek nazewniczych / części mowy

IOB
- O - brak jednostki nazewniczej
- I - kontynuacja jednostki
- B - początek nowej jednostki

Typy jednostek
- LOC - lokalizacja
- PER - osoba
- ORG - organizacja

Jeśli jest to jednoznaczne to nawet na początku jednostki daje się "I" \
"B" używa się zazwyczaj przy sytuacjach w których mogło być to niejednoznaczne

## Zadanie 3

Sklonuj repozytorium https://git.wmi.amu.edu.pl/kubapok/en-ner-conll-2003

Stwórz model *sequence labelling* realizujący zadanie NER, oparty o dowolną rekurencyjną sieć neuronową (możesz wzorować się na przykładzie z zajęć).

W plikach dev-0/out.tsv oraz test-A/out.tsv umieść wyniki predykcji dla dev-0/in.tsv i test-A/in.tsv odpowiednio.
Do ewaluacji wykorzystaj narzędzie GEval (https://gitlab.com/filipg/geval):

    wget https://gonito.net/get/bin/geval
    chmod u+x geval
    ./geval --help

Liczba punktów uzyskanych za zadanie zależy od uzyskanej wartości accuracy na zbiorze `test-A` (wynik zaokrąglony w górę):

    points = math.ceil(accuracy * 7.0)

⚠️ W systemie Moodle proszę załączyć plik `test-A/out.tsv` oraz link do repozytorium z rozwiązaniem zadania.


### Podejście softmax z embeddingami na przykładzie NER

In [337]:
%pip install -v torch torchtext --index-url https://download.pytorch.org/whl/cu118
%pip install -v datasets

Using pip 24.0 from C:\Users\Karol\AppData\Roaming\Python\Python311\site-packages\pip (python 3.11)
Defaulting to user installation because normal site-packages is not writeable
Looking in indexes: https://download.pytorch.org/whl/cu118
Note: you may need to restart the kernel to use updated packages.
Using pip 24.0 from C:\Users\Karol\AppData\Roaming\Python\Python311\site-packages\pip (python 3.11)
Defaulting to user installation because normal site-packages is not writeable
Note: you may need to restart the kernel to use updated packages.


In [338]:
from collections import Counter

import torch
from torchtext.vocab import vocab
from tqdm.notebook import tqdm
import pandas as pd

In [340]:
train_data = pd.read_csv("train/train.tsv", sep="\t", header=None, names=["y", "x"])
training_data = []
training_labels = []
for (labels,data) in train_data.iterrows():
    rowtokens = data["x"].split(" ")
    rowlabels = data["y"].split(" ")
    for i in range(len(rowtokens)):
        rowtokens[i] = rowtokens[i].lower()
    training_data.append(rowtokens)
    training_labels.append(rowlabels)

print(training_data[1])
print(len(training_data[1]))
print(training_labels[1])
print(len(training_labels[1]))

['rare', 'hendrix', 'song', 'draft', 'sells', 'for', 'almost', '$', '17,000', '.', '</s>', 'london', '1996-08-22', '</s>', 'a', 'rare', 'early', 'handwritten', 'draft', 'of', 'a', 'song', 'by', 'u.s.', 'guitar', 'legend', 'jimi', 'hendrix', 'was', 'sold', 'for', 'almost', '$', '17,000', 'on', 'thursday', 'at', 'an', 'auction', 'of', 'some', 'of', 'the', 'late', 'musician', "'s", 'favourite', 'possessions', '.', '</s>', 'a', 'florida', 'restaurant', 'paid', '10,925', 'pounds', '(', '$', '16,935', ')', 'for', 'the', 'draft', 'of', '"', 'ai', "n't", 'no', 'telling', '"', ',', 'which', 'hendrix', 'penned', 'on', 'a', 'piece', 'of', 'london', 'hotel', 'stationery', 'in', 'late', '1966', '.', '</s>', 'at', 'the', 'end', 'of', 'a', 'january', '1967', 'concert', 'in', 'the', 'english', 'city', 'of', 'nottingham', 'he', 'threw', 'the', 'sheet', 'of', 'paper', 'into', 'the', 'audience', ',', 'where', 'it', 'was', 'retrieved', 'by', 'a', 'fan', '.', '</s>', 'buyers', 'also', 'snapped', 'up', '16'

In [341]:
test_data = pd.read_csv("test-A/in.tsv", sep="\t", header=None, names=["x"])
testing_data = []
for (labels,data) in test_data.iterrows():
    rowtokens = data["x"].split(" ")
    for i in range(len(rowtokens)):
        rowtokens[i] = rowtokens[i].lower()
    testing_data.append(rowtokens)

print(testing_data[1])
print(len(testing_data[1]))

['rugby', 'union', '-', 'cuttitta', 'back', 'for', 'italy', 'after', 'a', 'year', '.', '</s>', 'rome', '1996-12-06', '</s>', 'italy', 'recalled', 'marcello', 'cuttitta', '</s>', 'on', 'friday', 'for', 'their', 'friendly', 'against', 'scotland', 'at', 'murrayfield', 'more', 'than', 'a', 'year', 'after', 'the', '30-year-old', 'wing', 'announced', 'he', 'was', 'retiring', 'following', 'differences', 'over', 'selection', '.', '</s>', 'cuttitta', ',', 'who', 'trainer', 'george', 'coste', 'said', 'was', 'certain', 'to', 'play', 'on', 'saturday', 'week', ',', 'was', 'named', 'in', 'a', '21-man', 'squad', 'lacking', 'only', 'two', 'of', 'the', 'team', 'beaten', '54-21', 'by', 'england', 'at', 'twickenham', 'last', 'month', '.', '</s>', 'stefano', 'bordon', 'is', 'out', 'through', 'illness', 'and', 'coste', 'said', 'he', 'had', 'dropped', 'back', 'row', 'corrado', 'covi', ',', 'who', 'had', 'been', 'recalled', 'for', 'the', 'england', 'game', 'after', 'five', 'years', 'out', 'of', 'the', 'natio

In [342]:
validate_data = pd.read_csv("dev-0/in.tsv", sep="\t", header=None, names=["x"])
validation_data = []
for (labels,data) in validate_data.iterrows():
    rowtokens = data["x"].split(" ")
    for i in range(len(rowtokens)):
        rowtokens[i] = rowtokens[i].lower()
    validation_data.append(rowtokens)

print(validation_data[1])

['cricket', '-', 'english', 'county', 'championship', 'scores', '.', '</s>', 'london', '1996-08-30', '</s>', 'result', 'and', 'close', 'of', 'play', 'scores', 'in', 'english', 'county', 'championship', 'matches', 'on', 'friday', ':', '</s>', 'leicester', ':', 'leicestershire', 'beat', 'somerset', 'by', 'an', 'innings', 'and', '39', 'runs', '.', '</s>', 'somerset', '83', 'and', '174', '(', 'p.', 'simmons', '4-38', ')', ',', 'leicestershire', '296', '.', '</s>', 'leicestershire', '22', 'points', ',', 'somerset', '4', '.', '</s>', 'chester-le-street', ':', 'glamorgan', '259', 'and', '207', '(', 'a.', 'dale', '69', ',', 'h.', 'morris', '69', ';', 'd.', 'blenkiron', '4-43', ')', ',', 'durham', '114', '(', 's.', 'watkin', '4-28', ')', 'and', '81-3', '.', '</s>', 'tunbridge', 'wells', ':', 'nottinghamshire', '214', '(', 'p.', 'johnson', '84', ';', 'm.', 'mccague', '4-55', ')', ',', 'kent', '108-3', '.', '</s>', 'london', '(', 'the', 'oval', ')', ':', 'warwickshire', '195', ',', 'surrey', '429

In [343]:
validate_labels = pd.read_csv("dev-0/expected.tsv", sep="\t", header=None, names=["y"])
validation_labels = []
for (labels,data) in validate_labels.iterrows():
    rowlabels = data["y"].split(" ")
    validation_labels.append(rowlabels)

print(validation_labels[1])

['O', 'O', 'B-MISC', 'I-MISC', 'I-MISC', 'O', 'O', 'O', 'B-LOC', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'B-MISC', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'B-LOC', 'O', 'B-ORG', 'O', 'B-ORG', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'B-ORG', 'O', 'O', 'O', 'O', 'B-PER', 'I-PER', 'O', 'O', 'O', 'B-ORG', 'O', 'O', 'O', 'B-ORG', 'O', 'O', 'O', 'B-ORG', 'O', 'O', 'O', 'B-LOC', 'O', 'B-ORG', 'O', 'O', 'O', 'O', 'B-PER', 'I-PER', 'O', 'O', 'B-PER', 'I-PER', 'O', 'O', 'B-PER', 'I-PER', 'O', 'O', 'O', 'B-ORG', 'O', 'O', 'B-PER', 'I-PER', 'O', 'O', 'O', 'O', 'O', 'O', 'B-LOC', 'I-LOC', 'O', 'B-ORG', 'O', 'O', 'B-PER', 'I-PER', 'O', 'O', 'B-PER', 'I-PER', 'O', 'O', 'O', 'B-ORG', 'O', 'O', 'O', 'B-LOC', 'O', 'B-LOC', 'I-LOC', 'O', 'O', 'B-ORG', 'O', 'O', 'B-ORG', 'O', 'O', 'B-PER', 'I-PER', 'O', 'O', 'O', 'O', 'B-PER', 'I-PER', 'O', 'O', 'B-PER', 'I-PER', 'O', 'O', 'B-PER', 'I-PER', 'O', 'O', 'B-PER', 'I-PER', 'O', 'O', 'O', 'O', 'B-LOC', 'O', 'B-ORG', 'O', 'O', 'B-PER', 'I-PER', 'O', 'O', 'B-PER'

In [344]:
NER_labels = {}
i = 0
for labels in training_labels:
    for label in labels:
        if label not in NER_labels:
            NER_labels[label] = i
            i += 1

NER_labels_reverse = {v: k for k, v in NER_labels.items()}
print(NER_labels)
print(NER_labels_reverse)

{'B-ORG': 0, 'O': 1, 'B-MISC': 2, 'B-PER': 3, 'I-PER': 4, 'B-LOC': 5, 'I-ORG': 6, 'I-MISC': 7, 'I-LOC': 8}
{0: 'B-ORG', 1: 'O', 2: 'B-MISC', 3: 'B-PER', 4: 'I-PER', 5: 'B-LOC', 6: 'I-ORG', 7: 'I-MISC', 8: 'I-LOC'}


Poniżej funkcja, która tworzy słownik (https://pytorch.org/text/stable/vocab.html).

Parametr `special` określa symbole specjalne:
* `<unk>` – nieznany token
* `<pad>` – wypełnienie
* `<bos>` – początek zdania
* `<eos>` – koniec zdania

In [346]:
def build_vocab(dataset):
    counter = Counter()
    for document in dataset:
        counter.update(document)
    return vocab(counter, specials=["<unk>", "<pad>", "<bos>", "<eos>"])

In [347]:
v = build_vocab(training_data)

In [348]:
itos = v.get_itos()  # mapowanie indeksów na tokeny

In [349]:
print(itos)

['<unk>', '<pad>', '<bos>', '<eos>', 'eu', 'rejects', 'german', 'call', 'to', 'boycott', 'british', 'lamb', '.', '</s>', 'peter', 'blackburn', 'brussels', '1996-08-22', 'the', 'european', 'commission', 'said', 'on', 'thursday', 'it', 'disagreed', 'with', 'advice', 'consumers', 'shun', 'until', 'scientists', 'determine', 'whether', 'mad', 'cow', 'disease', 'can', 'be', 'transmitted', 'sheep', 'germany', "'s", 'representative', 'union', 'veterinary', 'committee', 'werner', 'zwingmann', 'wednesday', 'should', 'buy', 'sheepmeat', 'from', 'countries', 'other', 'than', 'britain', 'scientific', 'was', 'clearer', '"', 'we', 'do', "n't", 'support', 'any', 'such', 'recommendation', 'because', 'see', 'grounds', 'for', ',', 'chief', 'spokesman', 'nikolaus', 'van', 'der', 'pas', 'told', 'a', 'news', 'briefing', 'he', 'further', 'study', 'required', 'and', 'if', 'found', 'that', 'action', 'needed', 'taken', 'by', 'proposal', 'last', 'month', 'farm', 'commissioner', 'franz', 'fischler', 'ban', 'brain

In [350]:
len(itos)  # liczba różnych tokenów w słowniku

21014

In [351]:
v["rejects"]  # indeks tokenu `on`

5

In [352]:
v["<unk>"]  # indeks nieznanego tokenu

0

W przypadku, gdy w analizowanym tekście znajdzie się token, którego nie ma w słowniku, będzie reprezentowany przez indeks domyślny (*default index*). Ustawiamy, żeby był taki sam, jak indeks „nieznanego tokenu”:

In [353]:
v.set_default_index(v["<unk>"])

In [354]:
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

In [355]:
def data_process(dt):
    # Wektoryzacja dokumentów tekstowych.
    return [
        torch.tensor(
            [v["<bos>"]] + [v[token] for token in document] + [v["<eos>"]],
            dtype=torch.long,
            device=device
        )
        for document in dt
    ]

In [356]:
def labels_process(dt):
    # Wektoryzacja etykiet (NER)
    return [torch.tensor([0] + document + [0], dtype=torch.long, device=device) for document in dt]

In [357]:
def get_NER_tags(labels_array):
    NER_tags = []
    for labels in labels_array:
        NER_tags.append([NER_labels[label] for label in labels])
    return NER_tags

def get_labels(NER_tags_array):
    labels = []
    for NER_tags in NER_tags_array:
        labels.append([NER_labels_reverse[tag] for tag in NER_tags])
    return labels

In [358]:
training_NER_tags = get_NER_tags(training_labels)
training_labels_from_NER_tags = get_labels(training_NER_tags)
print(training_NER_tags[1])
print(training_labels[1])
print(training_labels_from_NER_tags[1])
print(len(training_NER_tags[1]))
print(len(training_labels[1]))

[1, 3, 1, 1, 1, 1, 1, 1, 1, 1, 1, 5, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 5, 1, 1, 3, 4, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 5, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 2, 7, 7, 7, 1, 1, 1, 3, 1, 1, 1, 1, 1, 5, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 2, 1, 1, 5, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 3, 1, 1, 1, 3, 4, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 3, 1, 1, 1, 1, 1, 1, 1, 1, 2, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1]
['O', 'B-PER', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'B-LOC', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'B-LOC', 'O', 'O', 'B-PER', 'I-PER', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'B-LOC', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'B-MISC', 'I-MISC', 'I-MISC', 'I-MISC', 'O', 'O', 'O', 'B-

In [359]:
validation_NER_tags = get_NER_tags(validation_labels)
print(validation_NER_tags[1])
print(validation_labels[1])
print(len(validation_NER_tags[1]))
print(len(validation_labels[1]))

[1, 1, 2, 7, 7, 1, 1, 1, 5, 1, 1, 1, 1, 1, 1, 1, 1, 1, 2, 1, 1, 1, 1, 1, 1, 1, 5, 1, 0, 1, 0, 1, 1, 1, 1, 1, 1, 1, 1, 0, 1, 1, 1, 1, 3, 4, 1, 1, 1, 0, 1, 1, 1, 0, 1, 1, 1, 0, 1, 1, 1, 5, 1, 0, 1, 1, 1, 1, 3, 4, 1, 1, 3, 4, 1, 1, 3, 4, 1, 1, 1, 0, 1, 1, 3, 4, 1, 1, 1, 1, 1, 1, 5, 8, 1, 0, 1, 1, 3, 4, 1, 1, 3, 4, 1, 1, 1, 0, 1, 1, 1, 5, 1, 5, 8, 1, 1, 0, 1, 1, 0, 1, 1, 3, 4, 1, 1, 1, 1, 3, 4, 1, 1, 3, 4, 1, 1, 3, 4, 1, 1, 3, 4, 1, 1, 1, 1, 5, 1, 0, 1, 1, 3, 4, 1, 1, 3, 4, 1, 1, 3, 4, 1, 1, 1, 0, 1, 1, 3, 4, 1, 1, 1, 5, 1, 0, 1, 1, 1, 1, 3, 4, 1, 1, 3, 4, 1, 1, 3, 4, 1, 1, 1, 0, 1, 1, 1, 1, 1, 5, 1, 0, 1, 1, 1, 1, 0, 1, 1, 3, 4, 1, 1, 3, 1, 1, 1, 1, 3, 4, 1, 1, 3, 4, 1, 1, 1, 5, 1, 0, 1, 1, 1, 1, 3, 4, 1, 1, 1, 1, 1, 0, 1, 1, 3, 4, 1, 1, 3, 4, 1, 1, 1, 1]
['O', 'O', 'B-MISC', 'I-MISC', 'I-MISC', 'O', 'O', 'O', 'B-LOC', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'B-MISC', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'B-LOC', 'O', 'B-ORG', 'O', 'B-ORG', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'B-OR

Teraz wektoryzujemy wszystkie dane:

In [360]:
train_tokens_ids = data_process(training_data)
test_tokens_ids = data_process(testing_data)
validation_tokens_ids = data_process(validation_data)

In [361]:
train_labels = labels_process(training_NER_tags)
validation_labels = labels_process(validation_NER_tags)

Przykład, jak wyglądają dane po zwektoryzowaniu:

In [362]:
print(train_tokens_ids[1])
print(training_data[1])

tensor([  2, 257, 258, 259, 260, 261,  72, 262, 263, 264,  12,  13, 265,  17,
         13,  81, 257, 177, 266, 260, 163,  81, 259,  95, 267, 268, 269, 270,
        258,  59, 271,  72, 262, 263, 264,  22,  23, 158, 159, 272, 163, 253,
        163,  18, 273, 274,  42, 275, 276,  12,  13,  81, 277, 278, 279, 280,
        281, 132, 263, 282, 134,  72,  18, 260, 163,  61, 283,  64, 284, 285,
         61,  73, 189, 258, 286,  22,  81, 287, 163, 265, 288, 289, 233, 273,
        290,  12,  13, 158,  18, 291, 163,  81, 292, 293, 294, 233,  18, 295,
        296, 163, 297,  84, 298,  18, 299, 163, 300, 301,  18, 302,  73, 303,
         24,  59, 304,  95,  81, 305,  12,  13, 306, 307, 308, 309, 310,  55,
        311,  91, 312, 313, 309,  72, 272,  95, 258,  42, 314, 315, 316, 317,
         73, 318, 319,  26, 320,  53, 290,   8, 321,  12,  13, 322, 323,  81,
        324, 325,  88, 326, 163, 327, 328, 329, 330,  95, 258,   8, 331, 139,
        332,  73, 189, 159, 333, 334, 335, 336,  72, 337, 281, 1

In [363]:
train_tokens_ids[0]

tensor([  2,   4,   5,   6,   7,   8,   9,  10,  11,  12,  13,  14,  15,  13,
         16,  17,  13,  18,  19,  20,  21,  22,  23,  24,  25,  26,   6,  27,
          8,  28,   8,  29,  10,  11,  30,  31,  32,  33,  34,  35,  36,  37,
         38,  39,   8,  40,  12,  13,  41,  42,  43,   8,  18,  19,  44,  42,
         45,  46,  47,  48,  21,  22,  49,  28,  50,  51,  52,  53,  54,  55,
         56,  57,  30,  18,  58,  27,  59,  60,  12,  13,  61,  62,  63,  64,
         65,  66,  67,  68,  69,  62,  63,  64,  70,  66,  71,  72,  24,  73,
         61,  18,  20,  42,  74,  75,  76,  77,  78,  79,  80,  81,  82,  83,
         12,  13,  84,  21,  85,  58,  86,  59,  87,  88,  89,  24,  59,  90,
         91,  92,  59,  93,  24,  50,  38,  94,  95,  18,  19,  44,  12,  13,
         84,  21,  81,  96,  97,  98,  95,   4,  99, 100, 101, 102,   8, 103,
         40, 104,  73, 105,  88, 106, 107,  53,  18, 108,  88, 109, 110, 111,
         59,  81, 112, 113,  88, 114, 115,   8, 116, 108, 117,  

In [364]:
train_labels[0]

tensor([0, 0, 1, 2, 1, 1, 1, 2, 1, 1, 1, 3, 4, 1, 5, 1, 1, 1, 0, 6, 1, 1, 1, 1,
        1, 1, 2, 1, 1, 1, 1, 1, 2, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
        5, 1, 1, 1, 1, 0, 6, 1, 1, 1, 3, 4, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 5,
        1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
        1, 1, 1, 1, 0, 1, 1, 1, 3, 4, 4, 4, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
        1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 0, 6, 1, 1, 1, 1, 1, 1,
        1, 1, 1, 0, 1, 1, 3, 4, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
        1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 3, 1, 2, 1, 1, 1, 1, 5, 1, 5, 1,
        1, 1, 1, 1, 1, 1, 2, 7, 7, 1, 2, 1, 1, 1, 1, 1, 1, 1, 1, 3, 1, 1, 1, 1,
        1, 1, 1, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
        1, 1, 1, 1, 1, 1, 1, 1, 2, 1, 1, 3, 4, 4, 1, 1, 1, 3, 1, 1, 0, 1, 1, 1,
        1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 5, 1, 5, 1, 3, 1, 1, 1, 1,
        1, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1,

Funkcja, której użyjemy do ewaluacji:

In [365]:
def get_scores(y_true, y_pred):
    # Funkcja zwraca precyzję, pokrycie i F1
    acc_score = 0
    tp = 0
    fp = 0
    selected_items = 0
    relevant_items = 0

    for p, t in zip(y_pred, y_true):
        if p == t:
            acc_score += 1

        if p > 0 and p == t:
            tp += 1

        if p > 0:
            selected_items += 1

        if t > 0:
            relevant_items += 1

    if selected_items == 0:
        precision = 1.0
    else:
        precision = tp / selected_items

    if relevant_items == 0:
        recall = 1.0
    else:
        recall = tp / relevant_items

    if precision + recall == 0.0:
        f1 = 0.0
    else:
        f1 = 2 * precision * recall / (precision + recall)

    return precision, recall, f1

Ile mamy różnych tagów NER?

In [366]:
num_tags = max([max(x) for x in training_NER_tags]) + 1
print(num_tags)

9


Implementacja rekurencyjnej sieci neuronowej LSTM:

In [367]:
class LSTM(torch.nn.Module):

    def __init__(self):
        super(LSTM, self).__init__()
        self.emb = torch.nn.Embedding(len(v.get_itos()), 100, device=device)
        self.rec = torch.nn.LSTM(100, 256, 1, batch_first=True, device=device)
        self.fc1 = torch.nn.Linear(256, num_tags, device=device)

    def forward(self, x):
        emb = torch.relu(self.emb(x))
        lstm_output, (h_n, c_n) = self.rec(emb)
        out_weights = self.fc1(lstm_output)
        return out_weights

Stworzenie modelu:

In [368]:
lstm = LSTM()

Definicja funkcji kosztu:

In [369]:
criterion = torch.nn.CrossEntropyLoss()

Definicja optymalizatora:

In [370]:
optimizer = torch.optim.Adam(lstm.parameters())

Funkcja do ewaluacji modelu:

In [371]:
def eval_model(dataset_tokens, dataset_labels, model):
    Y_true = []
    Y_pred = []
    for i in tqdm(range(len(dataset_labels))):
        batch_tokens = dataset_tokens[i].unsqueeze(0)
        tags = list(dataset_labels[i].cpu().numpy())
        Y_true += tags

        Y_batch_pred_weights = model(batch_tokens).squeeze(0)
        Y_batch_pred = torch.argmax(Y_batch_pred_weights, 1)
        Y_pred += list(Y_batch_pred.cpu().numpy())

    return get_scores(Y_true, Y_pred)

In [372]:
def predict(dataset_tokens, model):
    Y_pred = []
    for i in tqdm(range(len(dataset_tokens))):
        batch_tokens = dataset_tokens[i]

        Y_batch_pred_weights = model(batch_tokens)
        Y_batch_pred = torch.argmax(Y_batch_pred_weights, 1)
        Y_pred.append(list(Y_batch_pred.cpu().numpy()))

    return Y_pred

Uczenie modelu:

In [373]:
NUM_EPOCHS = 15

In [374]:
for i in range(NUM_EPOCHS):
    lstm.train()
    # for i in tqdm(range(500)):
    for i in tqdm(range(len(train_labels))):
        batch_tokens = train_tokens_ids[i].unsqueeze(0)
        tags = train_labels[i].unsqueeze(1)

        predicted_tags = lstm(batch_tokens)

        optimizer.zero_grad()
        loss = criterion(predicted_tags.squeeze(0), tags.squeeze(1))

        loss.backward()
        optimizer.step()

    lstm.eval()
    print(eval_model(validation_tokens_ids, validation_labels, lstm))

  0%|          | 0/945 [00:00<?, ?it/s]

  0%|          | 0/215 [00:00<?, ?it/s]

(0.8592481647898522, 0.8753202230259193, 0.8672097341581988)


  0%|          | 0/945 [00:00<?, ?it/s]

  0%|          | 0/215 [00:00<?, ?it/s]

...

  0%|          | 0/215 [00:00<?, ?it/s]

(0.9295474678176301, 0.9290046714888487, 0.9292759903905036)


  0%|          | 0/945 [00:00<?, ?it/s]

  0%|          | 0/215 [00:00<?, ?it/s]

(0.9291776688042248, 0.9279874924653405, 0.9285821992686696)


Ewaluacja:

In [375]:
eval_model(validation_tokens_ids, validation_labels, lstm)

  0%|          | 0/215 [00:00<?, ?it/s]

(0.9291776688042248, 0.9279874924653405, 0.9285821992686696)

In [376]:
validation_NER_tags_predicted = predict(validation_tokens_ids, lstm)
print(validation_NER_tags_predicted[1])
validation_labels_predicted = labels_process(validation_NER_tags_predicted)
print(validation_labels_predicted[1])
validation_labels_from_NER_tags = get_labels(validation_NER_tags_predicted)
print(validation_labels_from_NER_tags[1])

  0%|          | 0/215 [00:00<?, ?it/s]

[0, 1, 1, 2, 7, 7, 1, 1, 1, 5, 1, 1, 1, 1, 1, 1, 1, 1, 1, 2, 1, 7, 1, 1, 1, 1, 1, 5, 1, 0, 1, 0, 1, 1, 1, 1, 1, 1, 1, 1, 0, 1, 1, 6, 1, 5, 4, 6, 1, 1, 0, 6, 1, 1, 0, 1, 1, 1, 0, 1, 1, 1, 5, 1, 0, 1, 1, 1, 1, 3, 4, 1, 1, 3, 4, 1, 1, 3, 4, 4, 1, 1, 0, 1, 1, 3, 4, 1, 1, 1, 1, 1, 1, 3, 8, 1, 0, 6, 1, 3, 4, 1, 1, 3, 4, 4, 1, 1, 0, 6, 1, 1, 0, 1, 6, 8, 1, 1, 0, 1, 1, 3, 4, 1, 3, 4, 1, 1, 1, 1, 3, 4, 1, 1, 3, 4, 1, 1, 3, 4, 1, 1, 3, 4, 1, 1, 1, 1, 5, 1, 0, 1, 1, 3, 4, 1, 1, 3, 4, 1, 1, 3, 4, 4, 1, 1, 0, 6, 1, 5, 8, 1, 1, 1, 5, 1, 0, 1, 1, 1, 1, 3, 4, 1, 1, 3, 4, 1, 1, 3, 4, 1, 1, 1, 0, 1, 1, 3, 1, 1, 5, 1, 0, 1, 1, 3, 1, 3, 4, 1, 3, 4, 4, 1, 3, 1, 1, 1, 1, 3, 4, 1, 1, 3, 4, 4, 1, 1, 5, 1, 0, 1, 1, 3, 1, 3, 4, 1, 1, 1, 1, 1, 0, 1, 1, 3, 4, 1, 1, 3, 4, 1, 1, 1, 1, 0]
tensor([0, 0, 1, 1, 2, 7, 7, 1, 1, 1, 5, 1, 1, 1, 1, 1, 1, 1, 1, 1, 2, 1, 7, 1,
        1, 1, 1, 1, 5, 1, 0, 1, 0, 1, 1, 1, 1, 1, 1, 1, 1, 0, 1, 1, 6, 1, 5, 4,
        6, 1, 1, 0, 6, 1, 1, 0, 1, 1, 1, 0, 1, 1, 1, 5, 1, 0, 1, 1, 1, 

In [377]:
with open("dev-0/out.tsv", "w") as f:
    for row in validation_labels_from_NER_tags:
        f.write(" ".join(row[1:-1]) + "\n")

In [378]:
testing_NER_tags = predict(test_tokens_ids, lstm)
testing_labels_from_NER_tags = get_labels(testing_NER_tags)
test_labels = labels_process(testing_NER_tags)

  0%|          | 0/230 [00:00<?, ?it/s]

In [379]:
eval_model(test_tokens_ids, test_labels, lstm)

  0%|          | 0/230 [00:00<?, ?it/s]

(0.6708165354166231, 0.6767538406423198, 0.6737721083439986)

In [380]:
with open("test-A/out.tsv", "w") as f:
    for row in testing_labels_from_NER_tags:
        f.write(" ".join(row[1:-1]) + "\n")

In [381]:
print(testing_data[0])
print(testing_NER_tags[0][1:-1])
print(testing_labels_from_NER_tags[0][1:-1])

['soccer', '-', 'japan', 'get', 'lucky', 'win', ',', 'china', 'in', 'surprise', 'defeat', '.', '</s>', 'nadim', 'ladki', '</s>', 'al-ain', ',', 'united', 'arab', 'emirates', '1996-12-06', '</s>', 'japan', 'began', 'the', 'defence', 'of', 'their', 'asian', 'cup', 'title', 'with', 'a', 'lucky', '2-1', 'win', 'against', 'syria', 'in', 'a', 'group', 'c', 'championship', 'match', 'on', 'friday', '.', '</s>', 'but', 'china', 'saw', 'their', 'luck', 'desert', 'them', 'in', 'the', 'second', 'match', 'of', 'the', 'group', ',', 'crashing', 'to', 'a', 'surprise', '2-0', 'defeat', 'to', 'newcomers', 'uzbekistan', '.', '</s>', 'china', 'controlled', 'most', 'of', 'the', 'match', 'and', 'saw', 'several', 'chances', 'missed', 'until', 'the', '78th', 'minute', 'when', 'uzbek', 'striker', 'igor', 'shkvyrin', 'took', 'advantage', 'of', 'a', 'misdirected', 'defensive', 'header', 'to', 'lob', 'the', 'ball', 'over', 'the', 'advancing', 'chinese', 'keeper', 'and', 'into', 'an', 'empty', 'net', '.', '</s>', 